In [1]:
import numpy as np
import pandas as pd

df = pd.read_csv('./10feature_cpu.csv')
df_time = pd.read_csv('./csv/10feature_cpu_date.csv')
#df.describe()

In [2]:
from sklearn.preprocessing import MinMaxScaler, StandardScaler

scaler = StandardScaler()
col = list(map(str, df.columns))[:-1]
df_scaled = scaler.fit_transform(df[col])

df_scaled = pd.DataFrame(df_scaled)
df_scaled.columns = col

#print(df_scaled)

In [3]:
TEST_SIZE = 200

train = df_scaled[:-TEST_SIZE]
test = df_scaled[-TEST_SIZE:]

In [4]:
def make_dataset(data, label, window_size=80):
    feature_list = []
    label_list = []
    for i in range(len(data) - window_size - 1):
        feature_list.append(np.array(data.iloc[i:i+window_size]))
        label_list.append(np.array(data.iloc[i+1 : i+window_size + 1]))
    return np.array(feature_list), np.array(label_list)

In [5]:
feature_cols = col
#label_cols = ['fault']
window_size = 100

train_feature = train[feature_cols]
#train_label = train[label_cols]
test_feature = test[feature_cols]
#test_label = test[label_cols]
# train dataset
train_feature, train_label = make_dataset(train_feature, train_feature, window_size)

# train, validation set 생성
from sklearn.model_selection import train_test_split
x_train, x_valid, y_train, y_valid = train_test_split(train_feature, train_label, test_size=0.2)

x_train.shape, x_valid.shape
# ((6086, 20, 4), (1522, 20, 4))

# test dataset (실제 예측 해볼 데이터)
test_feature, test_label = make_dataset(test_feature, test_feature, window_size)
test_feature.shape, test_label.shape
# ((180, 20, 4), (180, 1))
x_train.shape, y_train.shape

((878, 100, 10), (878, 100, 10))

In [6]:
from keras.models import Sequential
from keras.layers import Dense
from keras.callbacks import EarlyStopping, ModelCheckpoint
from keras.layers import LSTM
from keras.utils import multi_gpu_model
import tensorflow as tf 
#tf.compat.v1.disable_eager_execution()

tf.device('/gpu:1')
model = Sequential()

model.add(LSTM(100, 
               input_shape=(train_feature.shape[1], train_feature.shape[2]), 
               
               return_sequences=True)
          )
#model.add(Dense(200))
#model.add(Dense(200))
#model.add(Dense(200))
model.add(Dense(30))
model.add(Dense(30))
model.add(Dense(30))
model.add(Dense(30))
model.add(Dense(10))
#model.add(Dense(10,activation='tanh'))
#model = multi_gpu_model(model,gpus=4)
#model = tf.distribute.MirroredStrategy(model)
#1레이어(10) act x 9.52
#2레 10 1 x ㄴ
#2레 10 10 9.85
#2fp 10 10 relu x 10.0
#tanh 23.x
#8레 200.... 10 x 10.0 

In [ ]:
import os
model_path = './'

model.compile(loss='mean_squared_error', optimizer='adam')
early_stop = EarlyStopping(monitor='val_loss', patience=4000)
filename = os.path.join(model_path, 'tmp_checkpoint.h5')
checkpoint = ModelCheckpoint(filename, monitor='val_loss', verbose=1, save_best_only=True, mode='auto')

history = model.fit(x_train, y_train, 
                    epochs=100000, 
                    batch_size=4096,
                    validation_data=(x_valid, y_valid), 
                    callbacks=[early_stop, checkpoint])

Epoch 1/100000
1/1 [==============================] - ETA: 0s - loss: 1.1477
Epoch 00001: val_loss improved from inf to 1.06980, saving model to ./tmp_checkpoint.h5
1/1 [==============================] - 1s 551ms/step - loss: 1.1477 - val_loss: 1.0698
Epoch 2/100000
1/1 [==============================] - ETA: 0s - loss: 0.9928
Epoch 00002: val_loss improved from 1.06980 to 0.95592, saving model to ./tmp_checkpoint.h5
1/1 [==============================] - 0s 186ms/step - loss: 0.9928 - val_loss: 0.9559
Epoch 3/100000
1/1 [==============================] - ETA: 0s - loss: 0.8893
Epoch 00003: val_loss improved from 0.95592 to 0.87508, saving model to ./tmp_checkpoint.h5
1/1 [==============================] - 0s 60ms/step - loss: 0.8893 - val_loss: 0.8751
Epoch 4/100000
1/1 [==============================] - ETA: 0s - loss: 0.8158
Epoch 00004: val_loss improved from 0.87508 to 0.81173, saving model to ./tmp_checkpoint.h5
1/1 [==============================] - 0s 60ms/step - loss: 0.8158 -

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Epoch 65157: val_loss did not improve from 0.00520
1/1 [==============================] - 0s 38ms/step - loss: 0.0025 - val_loss: 0.0052
Epoch 65158/100000
1/1 [==============================] - ETA: 0s - loss: 0.0025
Epoch 65158: val_loss did not improve from 0.00520
1/1 [==============================] - 0s 40ms/step - loss: 0.0025 - val_loss: 0.0052
Epoch 65159/100000
1/1 [==============================] - ETA: 0s - loss: 0.0025
Epoch 65159: val_loss did not improve from 0.00520
1/1 [==============================] - 0s 37ms/step - loss: 0.0025 - val_loss: 0.0053
Epoch 65160/100000
1/1 [==============================] - ETA: 0s - loss: 0.0025
Epoch 65160: val_loss did not improve from 0.00520
1/1 [==============================] - 0s 34ms/step - loss: 0.0025 - val_loss: 0.0053
Epoch 65161/100000
1/1 [==============================] - ETA: 0s - loss: 0.0025
Epoch 65161: val_loss did not improve from 0.00520
1/1 [==============================] - 0s 45ms/step - loss: 0.0025 - val_los

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Epoch 72851: val_loss did not improve from 0.00514
1/1 [==============================] - 0s 38ms/step - loss: 0.0024 - val_loss: 0.0054
Epoch 72852/100000
1/1 [==============================] - ETA: 0s - loss: 0.0024
Epoch 72852: val_loss did not improve from 0.00514
1/1 [==============================] - 0s 35ms/step - loss: 0.0024 - val_loss: 0.0054
Epoch 72853/100000
1/1 [==============================] - ETA: 0s - loss: 0.0024
Epoch 72853: val_loss did not improve from 0.00514
1/1 [==============================] - 0s 36ms/step - loss: 0.0024 - val_loss: 0.0053
Epoch 72854/100000
1/1 [==============================] - ETA: 0s - loss: 0.0024
Epoch 72854: val_loss did not improve from 0.00514
1/1 [==============================] - 0s 35ms/step - loss: 0.0024 - val_loss: 0.0053
Epoch 72855/100000
1/1 [==============================] - ETA: 0s - loss: 0.0023
Epoch 72855: val_loss did not improve from 0.00514
1/1 [==============================] - 0s 41ms/step - loss: 0.0023 - val_los

In [13]:
# weight 로딩
model.load_weights(filename)

# 예측
pred = model.predict(test_feature)

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

plt.figure(figsize=(12, 9))
plt.plot(test_label, label='actual')
plt.plot(pred, label='prediction')
plt.legend()
plt.show()